# Linear regression with `statmodels`

Let us read again the `tips.csv` file

In [ ]:
import pandas as pd

dtypes = {
    "sex": "category",
    "smoker": "category",
    "day": "category",
    "time": "category"
} 

df = pd.read_csv("tips.csv", dtype=dtypes)
df.head()

## One-hot encoding and scaling

In [ ]:
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler

# Let's one one encode
df_one_hot = pd.get_dummies(df, drop_first=True)

# And use min-max scaler only on the "total_bill" and "size" columns
df_one_hot.head()

col_transformer = ColumnTransformer(transformers=[
    ("standard_scaler", StandardScaler(), ["total_bill", "size"])
])
df_one_hot[["total_bill", "size"]] = col_transformer.fit_transform(df_one_hot)
df_one_hot.head()

In [ ]:
if 'tip' in df:
    # The vector of labels
    y = df_one_hot["tip"]
    # The matrix of features
    X = df_one_hot.drop("tip", axis="columns")

In [ ]:
X.head()

## OLS fit using `statmodels`

In [ ]:
import statsmodels.api as sm

# With statmodels, we need to actually add a constant column in order to fit the intercept
X = sm.add_constant(X)

model = sm.OLS(y, X)
results = model.fit()
results.summary()

This summary provides quite a lot of information about the fit.
Here are some explanations about this summary.
Note that similar kind of summaries are provided by any other statistical software (such as `R` or `SAS`, etc.)

The **upper left part** provides basic information about the **model fit**:

| Element | Description |
|:--------|:------------|
| `Dep. Variable` | Which variable is the label |
| `Model`	| What model we are using in the fit |
| `Method`	| How the parameters of the model were calculated |
| `No. Observations` | The number of observations (examples) |
| `DF Residuals` | Degrees of freedom of the residuals: Number of observations – number of parameters |
| `DF Model` | Number of parameters in the model (not including the constant term if present) |

The **upper right part** assesses the **goodness-of-fit**:

| Element              | Description |
|:---------------------|:-----------|
| `R-squared`          | The $R^2$ coefficient of determination. |
| `Adj. R-squared`     | The above value adjusted with the number of observations and the degrees-of-freedom of the residuals |
| `F-statistic` | The $F$-test statistic, which measures how significant the fit is (null hypothesis is all coefficients are zero) |
| `Prob (F-statistic)` | The $p$-value of the $F$-test |
| `Log-likelihood`     | The log of the likelihood function |
| `AIC`                | The Akaike Information Criterion. Adjusts the log-likelihood based on the number of observations and the complexity of the model |
| `BIC`	               | The Bayesian Information Criterion. Similar to the AIC, but has a higher penalty for models with more parameters. |

The **middle part** is a report for each of the **coefficients**

| Element | Description |
|:--------|:------------|
| First column with no name | The name of the coefficient in the model |
| `coef` | The estimated value of the coefficient |
| `std err` | The standard error of the estimate of the coefficient. |
| `t` |	The statistic of the $t$-test for the null-hypothesis that the coefficient = 0 |
| `P > \|t\|` | $p$-value of the $t$-test  |
| `[0.025  0.975]` | The lower and upper values of the 95% confidence interval |
 
And finally, the **lower part** is about the **distribution of the residuals**

| Element | Description |
|:--------|:------------|
| `Skewness` | A measure of the symmetry of the data about the mean. Standard Gaussian errors have skewness zero |
| `Kurtosis` | A measure of the "flatness" of the distribution. Kurtosis of standard Gaussian is 3. |
| `Omnibus` | D’Angostino’s test. It provides a combined statistical test for the presence of skewness and kurtosis. |
| `Prob(Omnibus)` | $p$-value for the Omnibus statistic |
| `Jarque-Bera`	| Another test statistic of the skewness and kurtosis |
| `Prob (JB)` | The $p$-value for the Jarque-Bera test |
| `Durbin-Watson` | A test for the presence of autocorrelation (correlated errors) |
| `Cond. No` | Condition number of the matrix of features |

## OLS fit using the `formula` API of `statmodels`

Another convenient API is the **formula** API

In [ ]:
import statsmodels.formula.api as smf

formula = "tip ~ total_bill + size + sex_Male + smoker_Yes + day_Sat + day_Sun + day_Thur + time_Lunch"
model = smf.ols(formula=formula, data=df_one_hot)
res = model.fit()
res.summary()

Such "formulas" have a grammar:
- Add `-1` in a formula to remove intercept
- Use `A * B` to add interaction (it means `A + B + A:B`)
- Use `C(A)` to use `A` as a categorical variable

In [ ]:
formula = "tip ~ total_bill + C(size) + sex_Male * smoker_Yes + day_Sat + day_Sun + day_Thur + time_Lunch"
model = smf.ols(formula=formula, data=df_one_hot)
res = model.fit()
res.summary()

## Extract information about a fit 

Quantities of interest can be extracted directly from the result of the model fit. 
Here are some examples:

In [ ]:
# Estimated parameters
res.params

In [ ]:
# Estimated standard-deviations
res.bse

In [ ]:
# R-squared
res.rsquared

In [ ]:
# Predicted values
import numpy as np
import matplotlib.pyplot as plt

plt.scatter(y, results.predict())
x = np.linspace(0, 10, 100)
plt.plot(x, x, lw=3, ls='--')
plt.xlabel("Ground truth", fontsize=12)
plt.ylabel("Predictions", fontsize=12)

## Fisher test

Many tests and statistical tools are available in `statmodels`, let's just give as an example the Fisher test

In [ ]:
formula = "tip ~ total_bill + size + sex_Male + smoker_Yes + day_Sat + day_Sun + day_Thur + time_Lunch"
model = smf.ols(formula=formula, data=df_one_hot)
res = model.fit()
res.summary()

In [ ]:
# The null hypothesis
H0 = "sex_Male = smoker_Yes = day_Sat = day_Sun = day_Thur = time_Lunch = 0"
print(res.f_test(H0))

In [ ]:
# The null hypothesis
H0 = "total_bill = size = 0"
print(res.f_test(H0))